In [2]:
import requests as req
from bs4 import BeautifulSoup
import json
import math
import pandas as pd
import re
import numpy as np
import os
import random
from sklearn.model_selection import train_test_split

# User input

In [3]:
num_tabs = 200  # number of tabs wanted for dataset (will be rounded up to nearest 50 as tabs are scraped per page)

# Functions

In [4]:
def get_request_ug(url):
    '''Makes a get request to the specified Ultimate Guitar URL and returns relevant JSON data'''
    
    # Send request
    res = req.get(url)
    
    # Extract tab data from response
    # Note: I didn't bother with error handling in this instance, but you could check response code == 200, for example
    soup = BeautifulSoup(res.content) # format response content
    
    # Use BeautifulSoup to find relevant element, then cast to json and drill down the Ultimate-Guitar-Specific heirarchy
    page_data = json.loads(soup.find("div", {'class': 'js-store'})['data-content'])['store']['page']['data']
    
    return page_data

In [5]:
def scrape_page(page):
    # query params
    order = 'hitstotal_desc'  # order by total hits, descending order. i.e. most popular -> least popular
    tab_type = 'Chords'  # filter tabs that provide chord progression information (case sensitive)
    path = 'https://www.ultimate-guitar.com/explore'  # base endpoint path
    
    # generate url for request
    query_params = 'order=' + order + '&page=' + str(page)  + '&type[]=' + tab_type
    url = path + '?' + query_params
    
    # make request
    page_data = get_request_ug(url)['data']
    
    # create hits dataframe (stored separately to tab data)
    hits = page_data['hits']  # hits are stored with unique id which is also found in tab data
    hits = [[int(r['id']), int(r['hits'])] for r in hits]  # prep list of lists to be read into pandas dataframe, cast id and hits to integer to align with tabs dataset
    hits = pd.DataFrame(hits, columns = ['id', 'hits']).set_index('id')  # set index to shared unique id

    # create tabs dataframe (one page of data)
    tabs = page_data['tabs']  # extract all tabs and their attributes
    df = pd.DataFrame(tabs, columns=tabs[0].keys()).set_index('id')  # set index to shared unique id

    # join hits and tab data together for one page
    df = df.join(hits)  # adds hits dataframe to tabs dataframe - left join takes place by default on (shared) index
    return df

In [6]:
def get_tab_metadata(num_tabs):  
    #calc number of pages to scrape
    num_pages = math.ceil(num_tabs / 50)  # 50 tabs per page
    
    # initiate master dataframe
    df = pd.DataFrame()

    for p in range(1, num_pages + 1):
        page_tabs = scrape_page(p)
        df = df.append(page_tabs)
    return df

In [7]:
def get_chords(song_data):
    '''
    get_chords takes song data, and
    - extracts each of the following sections: Intro, Verse 1-9, Chorus, Outro, Bridge
    - parses each section for chords
    - returns 
        if tab in correct format: a dataframe with two columns [section, chords]
        otherwise: empty dataframe
    output columns
    - section: contains the name of each section eg. Chorus (may be duplicated)
    - chords: contians a list of chords eg. ['Eb', 'Gm6', 'Fsus4', 'Bb']
    '''
    
    # regex patterns
    extract_verse_name = r'\[[VCIOB][ehnur][roti][srd][euog][se ]?(\d?)\]'  # extract name of section. eg. Chorus
    extract_verse_with_name = extract_verse_name + r'\\r\\n(.*?)\\r\\n\\r\\n'  # extract each verse name and tab content
    extract_chords = r'\[ch\](.*?)\[\/ch\]'  # extract chords from within chord and lyric data
    
    song_data = song_data.replace('\r', '\\r').replace('\n', '\\n');  # to work with regex parser
    sections = re.finditer(extract_verse_with_name, song_data)  # has form [ '[section_name]', 'lyrics_and_chords' ]

    song = []  # intialise to hold data for each section
    for s in sections:
        section_string = song_data[s.start(): s.end()]  # extract a verse (with its name) from song_data
        section = re.search(extract_verse_name, section_string)  # get verse name from string
        
        section_name = section.group(0)[1:-1]  # remove []  surrounding section_name
        chords = re.findall(extract_chords, section_string)  # extract chords from lyrics
        if (chords == []): # if no chords in section, skip over it
            continue
        section = {'section_name': section_name, 'chords': chords}  # save section name with its chords
        song.append(section)  # append to get a view for the whole song

    return pd.DataFrame(song)  # turn song into dataframe


In [8]:
def remove_duplicate_songs(df):
    '''
    takes a dataframe and removes all duplicate songs, keeping the most popular version only
    '''
    
    for i in df.song_id.unique():
        tmp = df[df['song_id'] == i]
        versions = tmp.id.unique().tolist()
        if len(versions) == 1:  # only one version
            continue
        else:
            max_row_id = tmp.loc[tmp['hits'].idxmax()].id  # get max row
            versions.remove(max_row_id)  # remove from versions list
            for v in versions:  # remove everything remaining
                indexes = tmp[tmp['id'] == v].index  # get index of corresponding rows
                df = df.drop(indexes, inplace=False)  # drop
    return df

#### Chord nomenclature reference
#TODO: Create and upload image explaining Ultimate Guitar chord structure

In [40]:
def to_triad(chord):
    '''
    convert a chord into a three-note chord (triad)
    eg. A7sus4 -> A
    eg. E#dim7 -> E#dim
    '''
    dim = False  # indicates a diminished chord
    
    # systematically take everything above chord modifiers, from right to left
    # if the modifiers don't exist, then the chord is returned unchanged
    if '/' in chord:  # eg. A#m7/F -> A#m7
        chord = chord.split('/')[0]
    if 'add' in chord:  # eg. Fmadd9 -> Fm
        chord = chord.split('add')[0]
    if 'sus' in chord:  # eg. Csus2 -> C
        chord = chord.split('sus')[0]
    if 'aug' in chord:  # eg. Baug -> B
        chord = chord.split('aug')[0]
    if 'maj' in chord:  # eg. Bbmaj7 -> Bb
        chord = chord.split('maj')[0]
    if 'dim' in chord:  # eg. A7dim -> A7
        chord = chord.split('dim')[0]
        dim = True  # flag for later, diminished chords are basic triads
    if '9' in chord:  # E9 -> E
        chord = chord.split('9')[0]
    if '7' in chord:  # C7 -> C
        chord = chord.split('7')[0]
    if '6' in chord:  # F6 -> F
        chord = chord.split('6')[0]
    if '5' in chord:  # G5 -> G
        chord = chord.split('5')[0]
    if '2' in chord:  # D2 -> D
        chord = chord.split('2')[0]
    
    # append 'dim' modifier if applicable
    if dim:
        chord = chord + 'dim'
        
    return chord
   

def get_section_score(section, key_chords):
    '''
    returns number of matches between a sequence of chords and a set of chords
    '''
    return sum([1 for chord in section if chord in set(key_chords)])


def get_key(section):
    '''
    get_key takes a list of triad chords
    returns 
        keys: an array of possible keys
    multiple keys are possible where a section has limited chords \
    (eg. only 2 chords that are shared among multiple keys)
    '''

    scores = []
    for key in key_chord_mapping.columns:
        key_chords = key_chord_mapping[key]  # get chords corresponding to key
        score = get_section_score(section, key_chords)  # get match score for section chords against this key
        
        item = {'key': key, 'score': score}
        scores.append(item)
    key = max(scores, key=lambda x: x['score'])['key']
    
    return key


def guitar_to_piano_chords(chords, capo):
    '''
    takes a list of guitar chords and adjusts them to piano based on the fret that the capo is on (1 semitone per fret)
    returns
        pitched_up_chords: a list of chords raised by n=capo semitones
    '''
    
    chords_pitch_adj = []
    for chord in chords:
        for semitone in range(capo):
            print(capo, chord)
            chord = adjust_pitch_by_semitone(chord=chord, pitch_up=True)
        chords_pitch_adj.append(chord)
   
    return chords_pitch_adj
    
    
def is_flat(chord):
    if len(chord) > 1 and chord[1] == 'b':
        return True
    else:
        return False


def is_sharp(chord):
    if len(chord) > 1 and chord[1] == '#':
        return True
    else:
        return False


def is_minor(chord):
    if 'm' in chord and 'dim' not in chord:  # chord is minor
        return True
    else:
        return False
    

def is_dim(chord):
    if 'dim' in chord:
        return True
    else:
        return False

    
def adjust_pitch_by_semitone(chord, pitch_up):
    '''
    takes a chord and pitches_up based on value or pitch_up (boolean)
    returns
        pitch-adjusted chord
    '''
    
    minor = is_minor(chord)
    dim = is_dim(chord)
    
    if minor:
        chord = chord[:-1]  # chop off m
    elif is_dim:
        chord = chord.split('dim')[0]  # chop off dim
    
    if pitch_up:
        switcher = {
            'A': 'A#',
            'A#': 'B',
            'Bb': 'B',
            'B': 'C',
            'Cb': 'C',
            'C': 'C#',
            'C#': 'D',
            'Db': 'D',
            'D': 'D#',
            'D#': 'E',
            'Eb': 'E',
            'E': 'F',
            'Fb': 'F',
            'F': 'F#',
            'F#': 'G',
            'Gb': 'G',
            'G': 'G#',
            'G#': 'A',
            'Ab': 'A',
        }
        
    elif not pitch_up:
        switcher = {
            'A#': 'A',
            'B': 'A#',
            'Cb': 'A#',
            'Bb': 'B',
            'C': 'B',
            'C#': 'C',
            'Db': 'C',
            'D': 'C#',
            'D#': 'D',
            'Eb': 'D',
            'E': 'D#',
            'Fb': 'D#',
            'F': 'E',
            'F#': 'F',
            'Gb': 'F',
            'G': 'F#',
            'G#': 'G',
            'Ab': 'G',
            'A': 'G#',
        }
        
    else:  # pitch_up not boolean, so return original chord
        return chord
    
    # get adjusted chord value
    chord = switcher.get(chord, None)

    if minor:
        chord = chord + 'm'  # add m back
    elif dim:
        chord = chord + 'dim'  # add dim back
    
    return chord


def chords_to_degree(chords, key, map_to_closest=False):
    '''
    chords_to_degree(chords, key)
    - maps chords in key provided scale degree (index of key_chord_mapping)
    '''
    chords_in_key = key_chord_mapping[key]
    chord_degrees = []
    for chord in chords:
        if chord in chords_in_key.to_list():
            degree = key_chord_mapping[chords_in_key==chord].index.to_numpy()[0]
        elif map_to_closest:
            chord = closest_chord_in_key(chord, key)
            degree = key_chord_mapping[chords_in_key==chord].index.to_numpy()[0]
        else:
            degree =  None
        chord_degrees.append(degree)
    
    return chord_degrees


def switch_notation(chord):
    """
    take a chord and switch to its equivalent notation 
    eg. A# -> Bb, Cb -> B, A#m -> G#m -> Abm
    if chord is not flat or sharp, pass through
    """
    
    minor = is_minor(chord)
    
    if minor:
        chord = chord[:-1]  # chop off m
        
    notation_switcher = {
        'A#': 'Bb',
        'D#': 'Eb',
        'G#': 'Ab',
        'C#': 'Db',
        'F#': 'Gb',
        'B': 'Cb',
        'Cb': 'B',
        'Gb': 'F#',
        'Db': 'C#',
        'Ab': 'G#',
        'Eb': 'D#',
        'Bb': 'A#'
    }
    
    chord = notation_switcher.get(chord, chord)

    if minor:
        chord = chord + 'm'
        
    return chord
    

def closest_chord_in_key(chord, key): 
    '''
    returning a close chord in key of the same chord quality (minor, major or diminished)
    '''
    
    chords_in_key = key_chord_mapping[key]

    if chord in chords_in_key:
        return chord
    elif is_dim(chord):  # chord degrees: 7
        # avoid while loop and retrieve correct diminised chord in key
        chord = chords_in_key[7]
        return chord
    else: # map to a closeby chord of same quality (minor or major)
        pitch_adj = [True, False]
        chords_in_key = chords_in_key.to_list()
        while chord not in chords_in_key and switch_notation(chord) not in chords_in_key:
            print(song, key, chord)
            chord = adjust_pitch_by_semitone(chord=chord, pitch_up=random.choice(pitch_adj))

    if chord in chords_in_key:  # check whether sharp or flat representation was correct
        return chord
    else:
        return switch_notation(chord)

# Begin scraping

In [41]:
DATA_DIR = os.path.join(os.getcwd(), '..', 'data')
DATA_EXTERNAL_DIR = os.path.join(DATA_DIR, 'external')
DATA_LOOKUPS_DIR = os.path.join(DATA_DIR, 'lookups')
DATA_PROCESSED_DIR = os.path.join(DATA_DIR, 'processed')
DATA_RAW_DIR = os.path.join(DATA_DIR, 'raw')
key_chord_mapping = pd.read_csv(os.path.join(DATA_LOOKUPS_DIR, 'musical_key-triad_chord_mapping.csv'), index_col='Degree')

md = get_tab_metadata(num_tabs)  # scrape ultimate guitar 'explore' page for metadata (md)
md.drop(labels=['recording', 'part', 'tab_access_type', 'version_description', 'tp_version'], axis=1, inplace=True)

chords = []
# loop through tabs, fetch tab data and parse into chords
for index, tab_url in md['tab_url'].iteritems():  # get index to use as foreign key
    
    # send get request and extract tab info
    tab_data = get_request_ug(tab_url)['tab_view']  # get tab data
    tab_content = tab_data['wiki_tab']['content']  # extract tab content
    
    # extract capo fret number to pitch up guitar chords to get the true chord
    try: 
        # eg. capo on 2nd fret, a chord that is denoted as Em is actually F#m (E -> F -> F#)
        capo = tab_data['meta']['capo']
    except KeyError: 
        # capo key not present in json response
        capo = 0
        
    # parse tab content to extract chord
    song = get_chords(tab_content)
    
    # create additional columns, or move to next URL if song is empty
    if song.empty:
        continue
    else:  # list multiplication to create new column of correct length
        song['id'] = pd.Series([index] * len(song), dtype='int64')  # to be used to reference metadata (foreign key)
        song['capo'] = pd.Series([capo] * len(song), dtype='int64')  # save capo with chords
        song['key'] = pd.Series([None] * len(song), dtype='str')
        song['chords_simplified'] = pd.Series([None] * len(song), dtype='str')
        song['chords_simplified_pitch_corrected'] = pd.Series([None] * len(song), dtype='str')
        song['chords_numeric'] = pd.Series([None] * len(song), dtype='str')
    
    
    # get alternate chord representations
    song_chords = []
    for ids, section in song['chords'].iteritems():
        simple_section = []
        simple_pitch_corrected_section = []
        for chord in section:
            simple_chord = to_triad(chord)
            simple_section.append(simple_chord)
        
        # pitch correct guitar chords
        simple_pitch_corrected_section = guitar_to_piano_chords(simple_section, capo)
        
        # add alternate chords to dataframe
        song.at[ids, 'chords_simplified'] = simple_section
        song.at[ids, 'chords_simplified_pitch_corrected'] = simple_pitch_corrected_section
        
        song_chords.extend(simple_pitch_corrected_section)

    # get key of song - assumed 1 key for entire song
    key = get_key(song_chords)
    
    # check if key (and chords) can be simplified
    key_changed = False
    if key in ['A#', 'D#', 'G#', 'C#', 'F#']:  # these keys can be represented more simply
        key = switch_notation(key)
        key_changed = True
    elif key in ['Cb']: # check separately to sharp keys to avoid needing to check if key is flat or sharp 
        key = switch_notation(key)
        key_changed = True
    
    if key_changed:  # update chords
        for ids, section in song['chords_simplified_pitch_corrected'].iteritems():
            sec = []
            for chord in section:
                sec.append(switch_notation(chord))
            song.at[ids, 'chords_simplified_pitch_corrected'] = sec
    # add song's key to each of its sections in the dataframe
    song['key'] = [key] * len(song)
    
    # loop through sections and make numeric
    for ids, section in song['chords_simplified_pitch_corrected'].iteritems():
        song.at[ids, 'chords_numeric'] = chords_to_degree(section, key, map_to_closest=True)
        
    # create chords: a list of song dataframes
    chords.append(pd.DataFrame(song))

1 C
1 Am
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 F
1 G
1 C
1 G
1 C
1 F
1 G
1 Am
1 F
1 G
1 E
1 Am
1 F
1 Am
1 F
1 C
1 G
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 F
1 G
1 C
1 G
1 C
1 F
1 G
1 Am
1 F
1 G
1 E
1 Am
1 F
1 Am
1 F
1 C
1 G
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 F
1 G
1 C
1 G
1 C
1 F
1 G
1 Am
1 F
1 G
1 E
1 Am
1 F
1 Am
1 F
1 C
1 G
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 F
1 G
1 C
1 G
1 C
1 F
1 G
1 Am
1 F
1 G
1 E
1 Am
1 F
1 Am
1 F
1 C
1 G
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 C
1 Am
1 F
1 G
1 C
1 G
1 C
1 F
1 G
1 Am
1 F
1 G
1 E
1 Am
  section_name                                             chords      id  \
0        Intro                                     [C, Am, C, Am]  198052   
1      Verse 1  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
2       Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
3      Verse 2  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
4       Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
5      Verse 3  [C, Am, 

  section_name                                             chords      id  \
0        Intro                                     [C, Am, C, Am]  198052   
1      Verse 1  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
2       Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
3      Verse 2  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
4       Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
5      Verse 3  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
6       Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
7      Verse 4  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
8       Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
9      Verse 5  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   

   capo key                                  chords_simplified  \
0     1  Db                                     [C, Am, C, Am]   
1     1  Db  [C, Am,

4                                     None   D B
  section_name                                             chords       id  \
0        Intro                                   [C, G, Am, C, G]  1086983   
1       Chorus            [Em, B7, Em, B7, Em, B7, Em, A7, Dm, G]  1086983   
2      Verse 2         [C, Em, Am, F, C, G, F, G, Am, F, C, G, C]  1086983   
3       Chorus            [Em, B7, Em, B7, Em, B7, Em, A7, Dm, G]  1086983   
4      Verse 3  [C, Em, Am, F, C, G, F, G, Am, F, C, G, C, F, ...  1086983   

   capo key                                  chords_simplified  \
0     2   D                                   [C, G, Am, C, G]   
1     2   D                [Em, B, Em, B, Em, B, Em, A, Dm, G]   
2     2   D         [C, Em, Am, F, C, G, F, G, Am, F, C, G, C]   
3     2   D                [Em, B, Em, B, Em, B, Em, A, Dm, G]   
4     2   D  [C, Em, Am, F, C, G, F, G, Am, F, C, G, C, F, ...   

                   chords_simplified_pitch_corrected  \
0                            

4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 D
4 D#
4 E
4 F
4 C
4 C#
4 D
4 D#
4 A
4 A#
4 B
4 C
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
4 G
4 G#
4 A
4 A#
4 D
4 D#
4 E
4 F
4 Em
4 Fm
4 F#m
4 Gm
4 C
4 C#
4 D
4 D#
  section_name                                chords      id  capo key  \
0        Intro                         [G, D, Em, C]  373896     4   B   
1      Verse 1                         [G, 

2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
2 C
2 C#
2 C
2 C#
2 F
2 F#
2 G
2 G#
  section_name                                             chords       id  \
0        Intro                        [D7, Dm, C, D7, Dm, C, G/B]  1198871   
1      Verse 1       [Am, C, Dm, G, G7, C, Em/B, Am, C, Dm, G, C]  1198871   
2       Chorus  [G, F, G, C, F, G, C, F, G, Am, D7, F, Fm, C, ...  1198871   
3   

...

1 G
1 Em
1 Bm
1 D
1 G
1 Em
1 Bm
1 D
1 C
1 D
1 C
1 D
1 C
1 D
1 G
1 D
1 Em
1 C
1 D
1 C
1 D
1 C
1 D
1 G
1 D
1 Em
1 C
1 D
1 G
1 G
1 Em
1 Bm
1 D
1 G
1 Em
1 Bm
1 D
1 C
1 D
1 C
1 D
1 C
1 D
1 G
1 D
1 Em
1 C
1 D
1 C
1 D
1 C
1 D
1 G
1 D
1 Em
1 C
1 D
1 A
1 A
1 F#m
1 C#m
1 E
  section_name                                             chords       id  \
0      Verse 1                     [G, Em7, Bm, D, G, Em7, Bm, D]  1678440   
1       Chorus  [C, D, C, D, C, D, G, D/F#, Em, C, D, C, D, C,...  1678440   
2      Verse 2                     [G, Em7, Bm, D, G, Em7, Bm, D]  1678440   
3       Chorus  [C, D, C, D, C, D, G, D/F#, Em, C, D, C, D, C,...  1678440   
4       Bridge                                   [A, F#m, C#m, E]  1678440   

   capo key                                  chords_simplified  \
0     1  Ab                       [G, Em, Bm, D, G, Em, Bm, D]   
1     1  Ab  [C, D, C, D, C, D, G, D, Em, C, D, C, D, C, D,...   
2     1  Ab                       [G, Em, Bm, D, G, Em, Bm, D]   
3  

2 A
2 A#
2 E
2 F
2 F#m
2 Gm
2 D
2 D#
2 A
2 A#
2 E
2 F
2 F#m
2 Gm
2 D
2 D#
2 A
2 A#
2 E
2 F
2 F#m
2 Gm
2 D
2 D#
2 A
2 A#
2 E
2 F
2 F#m
2 Gm
2 D
2 D#
2 B
2 C
  section_name                            chords      id  capo key  \
0        Verse      [A, E, F#m, D, A, E, F#m, D]  392130     2   B   
1      Verse 2  [A, E, F#m, D, A, E, F#m, D, B7]  392130     2   B   

                 chords_simplified   chords_simplified_pitch_corrected  \
0     [A, E, F#m, D, A, E, F#m, D]      [B, F#, G#m, E, B, F#, G#m, E]   
1  [A, E, F#m, D, A, E, F#m, D, B]  [B, F#, G#m, E, B, F#, G#m, E, C#]   

             chords_numeric  
0  [1, 5, 6, 4, 1, 5, 6, 4]  
1                      None   B C#
  section_name                            chords      id  capo key  \
0        Verse      [A, E, F#m, D, A, E, F#m, D]  392130     2   B   
1      Verse 2  [A, E, F#m, D, A, E, F#m, D, B7]  392130     2   B   

                 chords_simplified   chords_simplified_pitch_corrected  \
0     [A, E, F#m, D, A, E, F#m

  section_name                                            chords      id  \
0        Intro                                       [D, F#m, A]  202167   
1      Verse 1     [D, Bm, F#m, Em7, A, A7, D, Bm, F#m, Em7, Gm]  202167   
2       Chorus             [D, A7sus4, A, A7, G, D, A, A7, G, D]  202167   
3      Verse 2  [D, Bm, F#m, Em7, A, A7, D, Bm, F#m, Em7, A, A7]  202167   
4       Chorus             [D, A7sus4, A, A7, G, D, A, A7, G, D]  202167   
5      Verse 3     [D, Bm, F#m, Em7, Gm, D, Bm, F#m, Em7, A, A7]  202167   
6       Chorus             [D, A7sus4, A, A7, G, D, A, A7, G, D]  202167   
7        Outro                                            [D, D]  202167   

   capo key                             chords_simplified  \
0     0   D                                   [D, F#m, A]   
1     0   D    [D, Bm, F#m, Em, A, A, D, Bm, F#m, Em, Gm]   
2     0   D                [D, A, A, A, G, D, A, A, G, D]   
3     0   D  [D, Bm, F#m, Em, A, A, D, Bm, F#m, Em, A, A]   
4     0   

  section_name                          chords     id  capo key  \
0        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
1       Chorus  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
2        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
3        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
4       Chorus  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
5        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   

                chords_simplified chords_simplified_pitch_corrected  \
0  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
1  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
2  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
3  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
4  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
5  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   

  chords_numeric  
0           N

5                            None   E F
  section_name                          chords     id  capo key  \
0        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
1       Chorus  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
2        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
3        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
4       Chorus  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   
5        Verse  [E, A, G, B, E, E, A, G, B, E]  47489     0   E   

                chords_simplified chords_simplified_pitch_corrected  \
0  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
1  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
2  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
3  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
4  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B, E]   
5  [E, A, G, B, E, E, A, G, B, E]    [E, A, G, B, E, E, A, G, B,

In [42]:
song.head()  # an individual song

section_name                 chords     id  capo key      chords_simplified  \
0        Intro         [F, Bb, F, Gm]  11489     0   F         [F, Bb, F, Gm]   
1      Verse 1            [F, Am, Bb]  11489     0   F            [F, Am, Bb]   
2      Verse 2            [F, Am, Bb]  11489     0   F            [F, Am, Bb]   
3       Bridge  [Dm, C, Bb, Dm, F, C]  11489     0   F  [Dm, C, Bb, Dm, F, C]   
4        Outro                [Dm, C]  11489     0   F                [Dm, C]   

  chords_simplified_pitch_corrected      chords_numeric  
0                    [F, Bb, F, Gm]        [1, 4, 1, 2]  
1                       [F, Am, Bb]           [1, 3, 4]  
2                       [F, Am, Bb]           [1, 3, 4]  
3             [Dm, C, Bb, Dm, F, C]  [6, 5, 4, 6, 1, 5]  
4                           [Dm, C]              [6, 5]

In [43]:
chords = pd.concat(chords, axis=0, ignore_index=True)
chords  # all songs concatenated

section_name                                             chords      id  \
0           Intro                                     [C, Am, C, Am]  198052   
1         Verse 1  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
2          Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
3         Verse 2  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...  198052   
4          Chorus                     [F, Am, F, C, G, C, Am, C, Am]  198052   
...           ...                                                ...     ...   
1236        Intro                                     [F, Bb, F, Gm]   11489   
1237      Verse 1                                        [F, Am, Bb]   11489   
1238      Verse 2                                        [F, Am, Bb]   11489   
1239       Bridge                              [Dm, C, Bb, Dm, F, C]   11489   
1240        Outro                                            [Dm, C]   11489   

      capo key                                  chords_simplified  \
0        1  Db                                     [C, Am, C, Am]   
1        1  Db  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...   
2        1  Db                     [F, Am, F, C, G, C, Am, C, Am]   
3        1  Db  [C, Am, C, Am, F, G, C, G, C, F, G, Am, F, G, ...   
4        1  Db                     [F, Am, F, C, G, C, Am, C, Am]   
...    ...  ..                                                ...   
1236     0   F                                     [F, Bb, F, Gm]   
1237     0   F                                        [F, Am, Bb]   
1238     0   F                                        [F, Am, Bb]   
1239     0   F                              [Dm, C, Bb, Dm, F, C]   
1240     0   F                                            [Dm, C]   

                      chords_simplified_pitch_corrected  \
0                                    [Db, Bbm, Db, Bbm]   
1     [Db, Bbm, Db, Bbm, Gb, Ab, Db, Ab, Db, Gb, Ab,...   
2               [Gb, Bbm, Gb, Db, Ab, Db, Bbm, Db, Bbm]   
3     [Db, Bbm, Db, Bbm, Gb, Ab, Db, Ab, Db, Gb, Ab,...   
4               [Gb, Bbm, Gb, Db, Ab, Db, Bbm, Db, Bbm]   
...                                                 ...   
1236                                     [F, Bb, F, Gm]   
1237                                        [F, Am, Bb]   
1238                                        [F, Am, Bb]   
1239                              [Dm, C, Bb, Dm, F, C]   
1240                                            [Dm, C]   

                                        chords_numeric  
0                                         [1, 6, 1, 6]  
1     [1, 6, 1, 6, 4, 5, 1, 5, 1, 4, 5, 6, 4, 5, 4, 6]  
2                          [4, 6, 4, 1, 5, 1, 6, 1, 6]  
3     [1, 6, 1, 6, 4, 5, 1, 5, 1, 4, 5, 6, 4, 5, 1, 6]  
4                          [4, 6, 4, 1, 5, 1, 6, 1, 6]  
...                                                ...  
1236                                      [1, 4, 1, 2]  
1237                                         [1, 3, 4]  
1238                                         [1, 3, 4]  
1239                                [6, 5, 4, 6, 1, 5]  
1240                                            [6, 5]  

[1241 rows x 8 columns]

## Sanity checks

#### count degrees of scales (0 indicates there is an element that is not 1-7 inclusive)


In [44]:
import matplotlib.pyplot as plt

x = np.zeros(8)

v = [1, 2, 3, 4, 5, 6, 7]  # valid chord degrees
for j in chords['chords_numeric']:
    for y in range(1, len(x)):
        x[y] = x[y] + sum([1 if z == y else 0 for z in j])
    x[0] = x[0] + sum([1 if z not in v else 0 for z in j])

x = pd.DataFrame(x)
x.plot.bar();
for i, j in enumerate(x[0]):
    plt.text(i - 0.25, j + 10, str(int(j)))
plt.title('Number of each chord degree present in chords dataset');
# all chords are represented with numbers 1-7
# there are no missed chords (represented by index 0)
# most popular chords are 1,4,5,6 - matches a well-known fact about pop music

In [45]:
key_chord_mapping

A    A#    Bb      B     C    C#    Db      D    D#    Eb      E  \
Degree                                                                         
1           A    A#    Bb      B     C    C#    Db      D    D#    Eb      E   
2          Bm    Cm    Cm    C#m    Dm   D#m   Ebm     Em    Fm    Fm    F#m   
3         C#m    Dm    Dm    D#m    Em    Fm    Fm    F#m    Gm    Gm    G#m   
4           D    D#    Eb      E     F    F#    Gb      G    G#    Ab      A   
5           E     F     F     F#     G    G#    Ab      A    A#    Bb      B   
6         F#m    Gm    Gm    G#m    Am   A#m   Bbm     Bm    Cm    Cm    C#m   
7       G#dim  Adim  Adim  A#dim  Bdim  Cdim  Cdim  C#dim  Ddim  Ddim  D#dim   

           F    F#    Gb      G    G#    Ab  
Degree                                       
1          F    F#    Gb      G    G#    Ab  
2         Gm   G#m   Abm     Am   A#m   Bbm  
3         Am   A#m   Bbm     Bm    Cm    Cm  
4         Bb     B     B      C    C#    Db  
5          C    C#    Db      D    D#    Eb  
6         Dm   D#m   Ebm     Em    Fm    Fm  
7       Edim  Fdim  Fdim  F#dim  Gdim  Gdim

### Investigate metadata structure and data quality

In [46]:
md.head()  # metadata (scraped from Explore page of Ultimate Guitar)

song_id                  song_name  artist_id    artist_name    type  \
id                                                                              
198052    135952                 Hallelujah       9898   Jeff Buckley  Chords   
1956589  1710759                    Perfect      30232     Ed Sheeran  Chords   
1248578   346275                  All Of Me      11714    John Legend  Chords   
1137467   298037                 Let Her Go      21762      Passenger  Chords   
1086983   152656  Cant Help Falling In Love      11125  Elvis Presley  Chords   

         version  votes   rating        date    status  preset_id  \
id                                                                  
198052         2  44824  4.87497  1121385600  approved        125   
1956589        1  36611  4.86007  1488453515  approved      18913   
1248578        1  22063  4.83855  1369872001  approved      14737   
1137467        1  19703  4.85264  1331596801  approved       2333   
1086983        1  23795  4.86585  1314230401  approved       2368   

        tonality_name  verified  \
id                                
198052             Db         0   
1956589            Ab         0   
1248578            Em         0   
1137467            Em         0   
1086983             C         0   

                                                artist_url  \
id                                                           
198052   https://www.ultimate-guitar.com/artist/jeff_bu...   
1956589  https://www.ultimate-guitar.com/artist/ed_shee...   
1248578  https://www.ultimate-guitar.com/artist/john_le...   
1137467  https://www.ultimate-guitar.com/artist/passeng...   
1086983  https://www.ultimate-guitar.com/artist/elvis_p...   

                                                   tab_url type_name      hits  
id                                                                              
198052   https://tabs.ultimate-guitar.com/tab/jeff-buck...    Chords  33644276  
1956589  https://tabs.ultimate-guitar.com/tab/ed-sheera...    Chords  29588299  
1248578  https://tabs.ultimate-guitar.com/tab/john-lege...    Chords  26737544  
1137467  https://tabs.ultimate-guitar.com/tab/passenger...    Chords  26624256  
1086983  https://tabs.ultimate-guitar.com/tab/elvis-pre...    Chords  23569240

In [47]:
md_columns = ['type', 'status', 'verified', 'type_name']
for c in md_columns:
    print(md[c].value_counts())

Chords    200
Name: type, dtype: int64
approved    200
Name: status, dtype: int64
0    200
Name: verified, dtype: int64
Chords    200
Name: type_name, dtype: int64


In [48]:
md = md.drop(md_columns, axis=1)
md = md.drop(['votes'], axis=1)
md.head()

song_id                  song_name  artist_id    artist_name  \
id                                                                      
198052    135952                 Hallelujah       9898   Jeff Buckley   
1956589  1710759                    Perfect      30232     Ed Sheeran   
1248578   346275                  All Of Me      11714    John Legend   
1137467   298037                 Let Her Go      21762      Passenger   
1086983   152656  Cant Help Falling In Love      11125  Elvis Presley   

         version   rating        date  preset_id tonality_name  \
id                                                               
198052         2  4.87497  1121385600        125            Db   
1956589        1  4.86007  1488453515      18913            Ab   
1248578        1  4.83855  1369872001      14737            Em   
1137467        1  4.85264  1331596801       2333            Em   
1086983        1  4.86585  1314230401       2368             C   

                                                artist_url  \
id                                                           
198052   https://www.ultimate-guitar.com/artist/jeff_bu...   
1956589  https://www.ultimate-guitar.com/artist/ed_shee...   
1248578  https://www.ultimate-guitar.com/artist/john_le...   
1137467  https://www.ultimate-guitar.com/artist/passeng...   
1086983  https://www.ultimate-guitar.com/artist/elvis_p...   

                                                   tab_url      hits  
id                                                                    
198052   https://tabs.ultimate-guitar.com/tab/jeff-buck...  33644276  
1956589  https://tabs.ultimate-guitar.com/tab/ed-sheera...  29588299  
1248578  https://tabs.ultimate-guitar.com/tab/john-lege...  26737544  
1137467  https://tabs.ultimate-guitar.com/tab/passenger...  26624256  
1086983  https://tabs.ultimate-guitar.com/tab/elvis-pre...  23569240

In [49]:
md[md.index == chords['id'][0]]  # using id from song table to read from metadata df

song_id   song_name  artist_id   artist_name  version   rating  \
id                                                                       
198052   135952  Hallelujah       9898  Jeff Buckley        2  4.87497   

              date  preset_id tonality_name  \
id                                            
198052  1121385600        125            Db   

                                               artist_url  \
id                                                          
198052  https://www.ultimate-guitar.com/artist/jeff_bu...   

                                                  tab_url      hits  
id                                                                   
198052  https://tabs.ultimate-guitar.com/tab/jeff-buck...  33644276

# Save chord progressions and tab metadata

In [50]:
# save chords to csv
chords.to_csv(os.path.join(DATA_RAW_DIR, 'tab_chords_by_section.csv'))

# save metadata to csv
md.to_csv(os.path.join(DATA_RAW_DIR, 'tab_metadata.csv'))


# Investigate data quality, clean up

In [51]:
df = chords.join(md, on='id')
df = remove_duplicate_songs(df)

In [52]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1077 entries, 0 to 1240
Data columns (total 20 columns):
section_name                         1077 non-null object
chords                               1077 non-null object
id                                   1077 non-null int64
capo                                 1077 non-null int64
key                                  1077 non-null object
chords_simplified                    1077 non-null object
chords_simplified_pitch_corrected    1077 non-null object
chords_numeric                       1077 non-null object
song_id                              1077 non-null int64
song_name                            1077 non-null object
artist_id                            1077 non-null int64
artist_name                          1077 non-null object
version                              1077 non-null int64
rating                               1077 non-null float64
date                                 1077 non-null object
preset_id                  

In [53]:
df.isna().sum()

section_name                         0
chords                               0
id                                   0
capo                                 0
key                                  0
chords_simplified                    0
chords_simplified_pitch_corrected    0
chords_numeric                       0
song_id                              0
song_name                            0
artist_id                            0
artist_name                          0
version                              0
rating                               0
date                                 0
preset_id                            0
tonality_name                        0
artist_url                           0
tab_url                              0
hits                                 0
dtype: int64

# Prepare training and test datasets for ML

In [54]:
# take slice
df = df[['chords_numeric', 'hits']]
df = df.reset_index()

# split into test and train
X = df.chords_numeric
y = df.hits
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2)

# Save training and test sets

In [55]:
# save training data to csv
X_train.to_csv(os.path.join(DATA_PROCESSED_DIR, 'train', 'X_train.csv'), header=True)
y_train.to_csv(os.path.join(DATA_PROCESSED_DIR, 'train', 'y_train.csv'), header=True)

# save test data to csv
X_test.to_csv(os.path.join(DATA_PROCESSED_DIR, 'test', 'X_test.csv'), header=True)
y_test.to_csv(os.path.join(DATA_PROCESSED_DIR, 'test', 'y_test.csv'), header=True)